This notebook creates a FASTA SNP matrix for each conserved core gene by genome.
Each genome will have a string of positions corresponding to a detected snp.
These are made using the MUSCLE alignments. This is to make it so that SNPs are
not detected between alleles, and instead, are true and unique to the 'core' genome.

In [1]:
import os
from Bio import SeqIO

In [2]:
alndir = './../core_genome/muscle_alignments2/' #alignment directory
filelist = [i for i in os.listdir(alndir) if i.endswith('.afa')]
print(len(filelist))

2413


In [11]:
#Create a new SNP matrix from the alignment

genomes =  [i.split('_')[0] for i in os.listdir('./../core_genome/FASTA_extractions_set_CCG')
            if i.endswith('.fasta')] #genomes queried
gc = len(genomes) #genome count

snpm = [] #snpmatrix - the step before the final output - ordered array
for i in range(gc):
    snpm.append([]) #start a new list for each genome

for item in filelist:
    print(item,'is being analyzed')
    records = SeqIO.parse(alndir+item, 'fasta')
    rd = SeqIO.to_dict(records) #dictionary of records with seq name as handle
    keys = list(rd.keys()) #keys in the dictionary (genomes)
    kc = [keys.count(i) for i in keys] #count instances of each entry to avoid duplicates
    if len(rd.keys()) != gc: #ignore those without 449 entries (length of our database)
        print('Too few or too many sequences in', item)
        continue
    elif any([True for i in kc if i!=1]):
        print('Dupes or empties(?) found in', item)
    else:
        pass
    
    #kick off the actual SNP finding mechanism
    
    sa = [] #Sequence array (see below)
    
    for genome in sorted(genomes): #the sorted list will keep the order straight
        
        #First step - build a structured array with each sequence for fast sorting.
        try:
            sequence = str(rd[genome].seq)
            sa.append(sequence)
        except:
            print(genome,'not in',item)
            break
    sl = len(sa[0]) #sequence length
    for i in range(sl):
        calls = [seq[i] for seq in sa] #base calls at position
        if any([True for base in calls if base == '-']): #ignore deletions/insertions
            print('\'-\' found, skipping.') #should appear somewhat often
            continue
        else:
            pass
        if len(set(calls)) == 1: #this is a no-SNP condition
            continue
        else:
            pass
        for j in range(gc): #append the sequence to the array
            snpm[j].append(calls[j])
            

NC_003197.2_prot_NP_462471.1_3466.afa is being analyzed
NC_003197.2_prot_NP_459314.1_309.afa is being analyzed
NC_003197.2_prot_NP_461868.1_2863.afa is being analyzed
Too few or too many sequences in NC_003197.2_prot_NP_461868.1_2863.afa
NC_003197.2_prot_NP_462228.1_3223.afa is being analyzed
NC_003197.2_prot_NP_461491.1_2486.afa is being analyzed
NC_003197.2_prot_NP_461802.1_2797.afa is being analyzed
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
NC_003197.2_prot_NP_461309.1_2304.afa is being analyzed
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, skipping.
'-' found, sk

In [12]:
#Write the snp matrix file
sg = sorted(genomes)

fl = [] #file lines

for i in range(gc):
    genome = sg[i]
    sequence = ''.join(snpm[i])
    header = '>'+genome
    fl.append(header)
    fl.append(sequence)
outfile = './../core_genome/ccg-muscle-SNPs.fasta'
with open(outfile, 'w') as f:
    f.write('\n'.join(fl))
    

In [10]:
#new number of keys - updated list
print(len(rd.keys()))

425


In [3]:
#Concatenating together the gene sequences for each genome
#This is to provide a more standard analysis -
#This supersedes the snp matrix as a matrix for analysis


#Need to collect, on a by gene basis, the sequences needed for each genome
#then glue them together and spit them out
#This will borrow heavily from the code above, hence why it's in the same notebook.

#Basically, it's the same except that we dont' mind having '-' characters.
#This may also affect branch lengths?
#We'll let RAxML deal with that!
#We are also not concerned with having meaningless positions - RAxML will take care of it!

genomes =  [i.split('_')[0] for i in os.listdir('./../core_genome/FASTA_extractions_set_CCG')
            if i.endswith('.fasta')] #genomes queried
gc = len(genomes) #genome count

#concatenated genome dictionary
#one entry per genome
#ID = genome name
cgd = {genome:[] for genome in genomes}

#For recordkeeping, make a list of the genes appended
gl = [] #gene list

#identify genes with one sequence hit per genome, append the sequence to the genome

for item in filelist:
    print(filelist.index(item)+1,'-',item,'is being analyzed')
    records = SeqIO.parse(alndir+item, 'fasta')
    rd = SeqIO.to_dict(records) #dictionary of records with seq name as handle
    keys = list(rd.keys()) #keys in the dictionary (genomes)
    kc = [keys.count(i) for i in keys] #count instances of each entry to avoid duplicates
    if len(rd.keys()) != gc: #ignore those without 449 entries (length of our database)
        print('Too few or too many sequences in', item)
        continue
    elif any([True for i in kc if i!=1]):
        print('Dupes or empties(?) found in', item)
        continue
    elif sorted(keys) != sorted(genomes):
        print('All genomes not found in', item,'???')
        continue
    else:
        pass
    
    #Now - append the sequences
    gl.append(item.split('.afa')[0]) #add gene to gene list
    for genome in genomes:
        cgd[genome].append(str(rd[genome].seq))

#starting new block - once cgd is built, don't need to rebuild

1 - NC_003197.2_prot_NP_462471.1_3466.afa is being analyzed
2 - NC_003197.2_prot_NP_459314.1_309.afa is being analyzed
3 - NC_003197.2_prot_NP_461868.1_2863.afa is being analyzed
Too few or too many sequences in NC_003197.2_prot_NP_461868.1_2863.afa
4 - NC_003197.2_prot_NP_462228.1_3223.afa is being analyzed
5 - NC_003197.2_prot_NP_461491.1_2486.afa is being analyzed
6 - NC_003197.2_prot_NP_461802.1_2797.afa is being analyzed
7 - NC_003197.2_prot_NP_461309.1_2304.afa is being analyzed
8 - NC_003197.2_prot_NP_462760.1_3756.afa is being analyzed
9 - NC_003197.2_prot_NP_459628.1_623.afa is being analyzed
10 - NC_003197.2_prot_NP_459693.1_688.afa is being analyzed
11 - NC_003197.2_prot_NP_459798.1_793.afa is being analyzed
12 - NC_003197.2_prot_NP_462379.1_3374.afa is being analyzed
13 - NC_003197.2_prot_NP_462507.1_3502.afa is being analyzed
14 - NC_003197.2_prot_NP_459666.1_661.afa is being analyzed
15 - NC_003197.2_prot_NP_460221.1_1216.afa is being analyzed
16 - NC_003197.2_prot_NP_461

In [5]:
#check lengths (should all be the same)
#will deal with the problem if it actually exists...

lenlist = []
for item in keys:
    lenlist.append([len(i) for i in cgd[item]]) #array, dimensions (#genomes & #genes)
    #this takes for each genome, the length of the sequence
for i in range(len(gl)):
    if len(set([j[i] for j in lenlist])) != 1:
        print(gl[i],'does not have all lengths equal!')
        continue
    else:
        pass

In [7]:
#make the genome files

destdir = './../core_genome/concat_ccg/'
for genome in genomes:
    with open(destdir+genome+'.fasta', 'w') as f:
        f.write(''.join(cgd[genome]))

In [8]:
#make a genomematrix file

destdir = './../core_genome/concat_ccg/'
with open(destdir+'all_matrix.fasta', 'w') as f:
    for genome in genomes:
        newlines = '>'+genome+'\n'+(''.join(cgd[genome]))+'\n'
        f.write(newlines)